In [1]:
# chose the current file directory as the working directory
import os

os.chdir("/teamspace/studios/this_studio/rubikscubesolver")

In [2]:
from tqdm import tqdm

import wandb  # for logging
import time
from dataclasses import dataclass

import jax
import jax.numpy as jnp
import flax.nnx as nnx

import optax

from rubiktransformer.model_diffusion_dt import RubikDTTransformer
import rubiktransformer.dataset as dataset
from rubiktransformer.trainer import reshape_sample

cuda_plugin_extension is not found.


In [3]:
@dataclass
class Config:
    """Configuration class"""

    jax_key: jnp.ndarray = jax.random.PRNGKey(47)
    rngs = nnx.Rngs(46)
    batch_size: int = 128
    lr_1: float = 4e-4
    lr_2: float = 4e-4
    nb_games: int = 128 * 100
    len_seq: int = 32
    nb_step: int = 1000000
    log_every_step: int = 10
    log_eval_every_step: int = 10
    log_policy_reward_every_step: int = 10
    add_data_every_step: int = 500

    save_model_every_step: int = 2000


config = Config()

# init wandb config
user = "forbu14"
project = "RubikTransformer"
display_name = "experiment_" + time.strftime("%Y%m%d-%H%M%S")

wandb.init(entity=user, project=project, name=display_name)

Failed to detect the name of this notebook, you can set it manually with the WANDB_NOTEBOOK_NAME environment variable to enable code saving.


wandb: Currently logged in as: forbu14. Use `wandb login --relogin` to force relogin


In [4]:
transformer = RubikDTTransformer(rngs=config.rngs, causal=True)

scheduler = optax.linear_schedule(init_value=0.0, end_value=1.0, transition_steps=4000)

# init optimizer
optimizer_dd = optax.chain(
    optax.clip_by_global_norm(1.0),
    #optax.lion(config.lr_1 / 10.0),
    optax.adamw(config.lr_1),
    optax.scale_by_schedule(scheduler),
)

optimizer_diffuser = nnx.Optimizer(transformer, optimizer_dd)

# metrics
metrics_train = nnx.MultiMetric(
    loss=nnx.metrics.Average("loss"),
    loss_cross_entropy=nnx.metrics.Average("loss_cross_entropy"),
)

metrics_eval = nnx.MultiMetric(
    loss_eval=nnx.metrics.Average("loss_eval"),

    loss_cross_entropy_eval=nnx.metrics.Average("loss_cross_entropy_eval"),
)

In [5]:
import pickle

filename = "state_ddt_model.pickle"

with open(filename, "rb") as input_file:
    state = pickle.load(input_file)

nnx.update(transformer, state)

In [5]:
# gather data from the environment
# init models and optimizers
env, buffer = dataset.init_env_buffer(sample_batch_size=config.batch_size)
env, buffer_eval = dataset.init_env_buffer(sample_batch_size=config.batch_size)


nb_games = config.nb_games
len_seq = config.len_seq

state_first = jnp.zeros((6, 3, 3))
state_next = jnp.zeros((len_seq, 6, 3, 3))
action = jnp.zeros((len_seq, 3))
action_proba = jnp.zeros((len_seq, 9))

# transform state to int8 type
state_first = state_first.astype(jnp.int8)
state_next = state_next.astype(jnp.int8)

# action to int32 type
action = action.astype(jnp.int32)

reward = jnp.zeros((1))

jit_step = jax.jit(env.step)

buffer_list = buffer.init(
    {
        "action": action,
        "reward": reward,
        "state_histo": state_next,
    }
)

buffer_list_eval = buffer_eval.init(
    {
        "action": action,
        "reward": reward,
        "state_histo": state_next,
    }
)

In [6]:
def step_fn(state, key):
    """
    Simple step function
    We choose a random action
    """

    action = jax.random.randint(
        key=key,
        minval=env.action_spec.minimum,
        maxval=env.action_spec.maximum,
        shape=(3,),
    )

    new_state, timestep = jit_step(state, action)
    timestep.extras["action"] = action

    return new_state, timestep


def run_n_steps(state, key, n):
    random_keys = jax.random.split(key, n)
    state, rollout = jax.lax.scan(step_fn, state, random_keys)

    return rollout


vmap_reset = jax.vmap(jax.jit(env.reset))
vmap_step = jax.vmap(run_n_steps, in_axes=(0, 0, None))

In [7]:
nnx.display(transformer)

In [8]:
key, subkey = jax.random.split(config.jax_key)
config.jax_key = key

buffer, buffer_list = dataset.fast_gathering_data_diffusion(
    env,
    vmap_reset,
    vmap_step,
    int(config.nb_games / 10),
    config.len_seq,
    buffer,
    buffer_list,
    subkey,
)

In [9]:
sample = buffer.sample(buffer_list, subkey)

def reshape_diffusion_setup(sample, key=jax.random.PRNGKey(0)):
    sample.experience["state_histo"] = sample.experience["state_histo"].reshape(
        (sample.experience["state_histo"].shape[0], sample.experience["state_histo"].shape[1], 54)
    )

    # one hot encoding for state_histo
    sample.experience["state_histo"] = jax.nn.one_hot(
        sample.experience["state_histo"],
        num_classes=6,
        axis=-1,
    )

    # batch creation
    batch  = sample.experience
    len_seq = batch["state_histo"].shape[1]

    time_step = jax.random.uniform(
        key, (batch["state_histo"].shape[0], 1, 1, 1)
    ) # random value between 0 and 1

    batch['time_step'] = time_step

    # now contact the value to have the context for the rectified flow setup
    batch["context"] = jnp.concatenate([batch["reward"], time_step[:, :, 0, 0]], axis=1)

    batch["state_past"] = batch["state_histo"][:, :len_seq//4, :, :]
    batch["state_future"] = batch["state_histo"][:, len_seq//4:, :, :]

    # now we generate the random noise for the rectified flow setup
    simplex_noise = jax.random.dirichlet(key, jnp.ones(6), batch["state_future"].shape[:-1])

    batch["state_future_noise"] = (
        (1 - time_step) * simplex_noise + time_step * batch["state_future"]
    )
    
    return batch


sample = reshape_diffusion_setup(sample)


In [10]:
def loss_fn_transformer_rf(model: RubikDTTransformer, batch):
    # rectified flow setup
    state_past, state_future = model(
        batch["state_past"], batch["state_future_noise"], batch["context"]
    )

    loss_crossentropy = optax.softmax_cross_entropy(
        logits=state_future, labels=batch["state_future"]
    ).mean(axis=[1, 2])

    weight = jnp.clip(1. / (1. - batch["time_step"][:, 0, 0, 0]), min=0.005, max=1.5)

    loss_cross_entropy_weight = loss_crossentropy * weight

    return loss_cross_entropy_weight.mean(), (loss_crossentropy.mean())


@nnx.jit
def train_step_transformer_rf(
    model: RubikDTTransformer,
    optimizer: nnx.Optimizer,
    metrics: nnx.MultiMetric,
    batch,
):
    """Train for a single step."""

    grad_fn = nnx.value_and_grad(loss_fn_transformer_rf, has_aux=True)
    (loss, (loss_crossentropy)), grads = grad_fn(model, batch)
    metrics.update(
        loss=loss, loss_cross_entropy=loss_crossentropy
    )
    optimizer.update(grads)

In [11]:
key, subkey = jax.random.split(config.jax_key)
config.jax_key = key

buffer, buffer_list = dataset.fast_gathering_data_diffusion(
    env,
    vmap_reset,
    vmap_step,
    config.nb_games * 15, # old is int(config.nb_games * 10.0),
    config.len_seq,
    buffer,
    buffer_list,
    subkey,
)

In [12]:
import pickle

# transformer model calibration
for idx_step in tqdm(range(config.nb_step)):
    # training for world model
    key, subkey = jax.random.split(config.jax_key)
    config.jax_key = key

    if idx_step % config.add_data_every_step == 0:
        buffer, buffer_list = dataset.fast_gathering_data_diffusion(
            env,
            vmap_reset,
            vmap_step,
            int(config.nb_games // 10),
            config.len_seq,
            buffer,
            buffer_list,
            config.jax_key,
        )

    sample = buffer.sample(buffer_list, subkey)
    sample = reshape_diffusion_setup(sample, subkey)

    # we update the policy
    train_step_transformer_rf(
        transformer, optimizer_diffuser, metrics_train, sample
    )

    if idx_step % config.log_every_step == 0:
        metrics_train_result = metrics_train.compute()
        print(metrics_train_result)

        wandb.log(metrics_train_result, step=idx_step)
        metrics_train.reset()

    if idx_step % config.log_eval_every_step == 0:
        key, subkey = jax.random.split(config.jax_key)
        config.jax_key = key

        buffer_eval, buffer_list_eval = dataset.fast_gathering_data_diffusion(
            env,
            vmap_reset,
            vmap_step,
            int(128),
            config.len_seq,
            buffer_eval,
            buffer_list_eval,
            subkey,
        )

        sample = buffer_eval.sample(buffer_list_eval, subkey)
        sample = reshape_diffusion_setup(sample, subkey)

        loss, (loss_crossentropy) = loss_fn_transformer_rf(
            transformer, sample
        )

        metrics_eval.update(
            loss_eval=loss,
            loss_cross_entropy_eval=loss_crossentropy,
        )
        wandb.log(metrics_eval.compute(), step=idx_step)

        metrics_eval.reset()

    if idx_step % config.save_model_every_step == 0:

        state_weight = nnx.state(transformer)

        with open("state_ddt_model.pickle", "wb") as handle:
            pickle.dump(state_weight, handle, protocol=pickle.HIGHEST_PROTOCOL)

{'loss': Array(0.32483298, dtype=float32), 'loss_cross_entropy': Array(0.28385186, dtype=float32)}


  1%|          | 5509/1000000 [15:34<89:07:51,  3.10it/s] 

{'loss': Array(0.32437667, dtype=float32), 'loss_cross_entropy': Array(0.2848944, dtype=float32)}


  1%|          | 5519/1000000 [15:36<41:30:26,  6.66it/s]

{'loss': Array(0.3191602, dtype=float32), 'loss_cross_entropy': Array(0.27801296, dtype=float32)}


...

{'loss': Array(0.13331732, dtype=float32), 'loss_cross_entropy': Array(0.12600248, dtype=float32)}


 11%|█         | 109549/1000000 [5:01:12<25:23:38,  9.74it/s]

{'loss': Array(0.13018058, dtype=float32), 'loss_cross_entropy': Array(0.12280568, dtype=float32)}


 11%|█         | 109559/1000000 [5:01:14<38:10:09,  6.48it/s]

{'loss': Array(0.14162515, dtype=float32), 'loss_cross_entropy': Array(0.13380678, dtype=float32)}


In [23]:

def sampling_model(key, model, sample_eval, nb_batch_explore=128, nb_step=100):
    """
    Function used to sampling a state from a list 
    """
    seq_len_future = sample_eval["state_future"].shape[1]
    noise_future  = jax.random.dirichlet(key, jnp.ones(6), (nb_batch_explore, seq_len_future, 54))
    sample_eval["reward"] = jnp.linspace(start=-0.5, stop=0.5, num=nb_batch_explore)[:, None]

    for t_step in range(nb_step):
        t_step_array = jnp.ones((nb_batch_explore, 1, 1, 1)) * float(t_step / nb_step)
        sample_eval["context"] = jnp.concatenate([sample_eval["reward"], t_step_array[:, :, 0, 0]], axis=1)

        estimation_logits_past, estimation_logits_future = model(
            sample_eval["state_past"], noise_future, sample_eval["context"]
        )


        estimation_proba_future = jax.nn.softmax(estimation_logits_future, axis=-1)

        noise_future = noise_future + float(1. / nb_step) * 1./ (1. - t_step_array + 0.0001) * (estimation_proba_future - noise_future)

        print(result.sum(axis=-1)[:10])

    return noise_future



In [48]:
key, subkey = jax.random.split(config.jax_key)
config.jax_key = key

sample = buffer.sample(buffer_list, subkey)
sample = reshape_diffusion_setup(sample, subkey)

In [49]:
key, subkey = jax.random.split(config.jax_key)
config.jax_key = key

sample = buffer.sample(buffer_list, subkey)
sample = reshape_diffusion_setup(sample, subkey)


result = sampling_model(key=config.jax_key, model=transformer, sample_eval=sample, nb_batch_explore=128, nb_step=100)
result

[[[1.         1.         1.         ... 0.9999999  1.         1.        ]
  [1.         1.0000001  1.         ... 1.         0.99999994 1.        ]
  [0.9999999  1.0000001  1.0000002  ... 0.99999994 0.9999999  0.99999994]
  ...
  [1.0000001  1.0000001  1.         ... 0.99999994 1.0000001  0.99999994]
  [1.         1.         1.0000001  ... 1.0000001  0.99999994 1.        ]
  [1.0000001  1.         1.         ... 0.99999994 1.         1.        ]]

 [[1.         1.         1.         ... 0.99999994 1.         1.0000001 ]
  [1.         1.         1.         ... 1.         0.9999999  1.0000001 ]
  [0.9999999  1.         0.99999994 ... 0.9999999  1.         0.99999994]
  ...
  [1.         0.99999994 1.         ... 0.9999998  1.         0.99999994]
  [0.99999994 1.         1.0000001  ... 1.         0.99999994 0.99999994]
  [0.99999994 1.         1.         ... 1.         0.99999994 1.        ]]

 [[1.         1.         1.0000001  ... 0.9999999  1.0000001  0.99999994]
  [1.         1.      

Array([[[[1.40354387e-05, 2.78135994e-05, 1.83428638e-05,
          1.19304750e-05, 9.99907136e-01, 2.07419507e-05],
         [5.35143045e-07, 9.99951959e-01, 2.02469528e-06,
          5.87257091e-06, 1.66611280e-05, 2.29480211e-05],
         [3.64724547e-05, 5.65210357e-05, 9.99861240e-01,
          1.56062742e-06, 2.86730938e-05, 1.55076850e-05],
         ...,
         [4.27688065e-07, 2.31107697e-05, 9.99951243e-01,
          9.32649709e-06, 8.20209971e-06, 7.77299283e-06],
         [1.63635705e-05, 9.99928594e-01, 1.97293703e-05,
          1.52112916e-05, 4.17535193e-06, 1.60298077e-05],
         [2.83019617e-05, 8.48784111e-06, 2.48276629e-05,
          1.59980264e-05, 3.40319239e-05, 9.99888361e-01]],

        [[6.94335205e-04, 3.26467765e-04, 2.68780859e-05,
          1.24215148e-05, 3.04284040e-05, 9.98909414e-01],
         [2.33147875e-06, 9.99922991e-01, 9.13714757e-06,
          1.21784396e-05, 3.90338246e-05, 1.43673969e-05],
         [3.58729763e-03, 9.76185441e-01, 1.8595

In [61]:
index_batch  = 63

jnp.argmax(sample["state_past"], axis=-1).reshape((128, 8, 6, 3, 3))[index_batch, -1, :, :, :]

Array([[[5, 2, 2],
        [0, 0, 0],
        [3, 1, 1]],

       [[4, 2, 4],
        [1, 1, 3],
        [0, 1, 2]],

       [[5, 2, 3],
        [2, 2, 4],
        [3, 1, 1]],

       [[0, 5, 2],
        [3, 3, 4],
        [0, 3, 0]],

       [[1, 3, 5],
        [5, 4, 5],
        [4, 4, 4]],

       [[1, 4, 5],
        [0, 5, 0],
        [3, 5, 2]]], dtype=int32)

In [56]:
jnp.argmax(result, axis=-1).reshape((128, 24, 6, 3, 3))[index_batch, 0, :, :, :]

Array([[[3, 4, 1],
        [0, 0, 0],
        [3, 1, 1]],

       [[4, 2, 4],
        [1, 1, 3],
        [0, 1, 2]],

       [[5, 2, 2],
        [2, 2, 5],
        [3, 1, 3]],

       [[0, 3, 0],
        [3, 3, 5],
        [0, 4, 2]],

       [[2, 3, 5],
        [2, 4, 5],
        [5, 4, 4]],

       [[1, 4, 5],
        [0, 5, 0],
        [1, 5, 4]]], dtype=int32)

In [55]:
jnp.argmax(result, axis=-1).reshape((128, 24, 6, 3, 3))[index_batch, 1, :, :, :]

Array([[[3, 4, 1],
        [0, 0, 0],
        [3, 1, 1]],

       [[4, 2, 4],
        [1, 1, 3],
        [0, 1, 2]],

       [[5, 2, 2],
        [2, 2, 5],
        [3, 1, 3]],

       [[0, 3, 0],
        [3, 3, 5],
        [0, 4, 2]],

       [[2, 3, 5],
        [2, 4, 5],
        [5, 4, 4]],

       [[1, 4, 5],
        [0, 5, 0],
        [1, 5, 4]]], dtype=int32)

In [ ]:
sample = buffer_eval.sample(buffer_list_eval, subkey)
sample = reshape_sample(sample)

TrajectoryBufferSample(experience={'action': Array([[[1.32556781e-01, 7.96739519e-01, 5.36718592e-02, ...,
         3.91646661e-03, 4.48901858e-03, 9.91594553e-01],
        [3.49070907e-01, 4.57749265e-04, 4.38157976e-01, ...,
         7.23136306e-01, 1.23497941e-01, 1.53365776e-01],
        [6.12441264e-03, 2.50436477e-02, 1.35732419e-03, ...,
         3.82237613e-01, 5.98694921e-01, 1.90675538e-02],
        ...,
        [1.41329234e-04, 2.44877161e-03, 8.43136787e-01, ...,
         2.33344346e-01, 6.42170012e-01, 1.24485560e-01],
        [6.32655225e-04, 1.77795421e-02, 9.65278149e-01, ...,
         1.25269741e-02, 3.21629345e-01, 6.65843725e-01],
        [9.08881542e-04, 1.04175135e-01, 7.50824576e-04, ...,
         9.99683421e-03, 7.89827347e-01, 2.00175866e-01]],

       [[2.03237548e-01, 7.00179100e-01, 3.63819454e-05, ...,
         9.96583939e-01, 2.39940570e-03, 1.01662707e-03],
        [7.63220847e-01, 1.11325733e-01, 3.15520242e-02, ...,
         5.45369804e-01, 4.54322606e-0

AttributeError: 'RubikTransformer' object has no attribute 'state_mapping'

In [14]:
# save buffer, buffer_list
# in pickle
import pickle

state_weight = nnx.state(transformer)

In [15]:
state_weight

State({
  'action_mapping': {
    'bias': VariableState(
      type=Param,
      value=Array([ 4.04955857e-02,  2.82790326e-02, -7.85927773e-02,  7.52160996e-02,
             -6.11112965e-03,  6.96982583e-03, -1.17343664e-02, -1.74523471e-03,
              1.28632234e-02, -7.83682019e-02,  2.75444221e-02, -4.00350802e-02,
              1.79233290e-02,  8.38570073e-02,  2.03401130e-02,  4.92124483e-02,
              8.69528428e-02,  2.20998153e-02, -3.42875794e-02, -6.76687211e-02,
              2.17811018e-02,  8.36544111e-02, -3.08539756e-02, -8.56901798e-03,
             -6.66830465e-02,  1.15918748e-01,  5.94779989e-03,  1.72799546e-02,
             -1.16014622e-01, -6.75882176e-02, -6.16184436e-02, -5.52975051e-02,
              4.17982265e-02, -5.43787293e-02,  1.19193546e-01, -9.40112211e-03,
             -4.03175130e-02, -3.47817354e-02, -6.77642366e-03,  8.85512680e-02,
              4.83243428e-02,  6.59283325e-02, -5.58541063e-03,  3.46533172e-02,
             -6.63223118e-02